In [1]:
## Import dependencies

import numpy as np
from os import path
import matplotlib.pyplot as plt
import os
import nmrglue as ng
import seaborn as sns
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import torch
import torch.nn as nn
import torch.optim as optim
import copy
import time
import optuna
import pandas as pd
from torch.cuda.amp import GradScaler, autocast


# Set default plot size
plt.rcParams["figure.figsize"] = (30,20)

## Optimize Transformer architecture and hyperparameters on dataset of 44 metabolites

In [2]:
# Define number of epochs used later in training (this will have to be redefined later......)
num_epochs = 700

# Name variable used for saving model metrics, name should reflect model used, dataset used, and other information such as # of epochs
ModelName = "Transformer_Opt_44Met_" + str(num_epochs) +"ep"

# Set the random seed
os.chdir('/home/htjhnson/Desktop/DL-NMR-Optimization/ModelPerformanceMetrics/')
seed = 1
torch.manual_seed(seed)
np.save(ModelName + "_Seed.npy", seed)

In [3]:
# Load training and testing datasets, validation datasets, and representative example spectra 

# Switch to directory containing datasets
os.chdir('/home/htjhnson/Desktop/DL-NMR-Optimization/GeneratedDataAndVariables')

# Load training data and max value from testing and training datasets
spectra = np.load('Dataset44_ExtendedRange_MoreLeftOut_Combined1Distribution_ForManuscript_Spec.npy')
conc1 = np.load('Dataset44_ExtendedRange_MoreLeftOut_Combined1Distribution_ForManuscript_Conc.npy')

spectraVal = np.load('Dataset44_ExtendedRange_MoreLeftOut_Combined1Distribution_ForManuscript_Val_Spec.npy')
concVal = np.load('Dataset44_ExtendedRange_MoreLeftOut_Combined1Distribution_ForManuscript_Val_Conc.npy')

In [4]:
## Prepare to switch data from CPU to GPU

# Check if CUDA (GPU support) is available
if torch.cuda.is_available():
    device = torch.device("cuda")          # A CUDA device object
    print("Using GPU for training.")
else:
    device = torch.device("cpu")           # A CPU object
    print("CUDA is not available. Using CPU for training.")

Using GPU for training.


In [5]:
## Set up data for testing and training

# Split into testing and training data
X_train, X_test, y_train, y_test = train_test_split(spectra, conc1, test_size = 0.2, random_state = 1)

# Tensorize and prepare datasets
X_train = torch.tensor(X_train).float()
y_train = torch.tensor(y_train).float()
X_test = torch.tensor(X_test).float()
y_test = torch.tensor(y_test).float()


# Move the input data to the GPU device
X_train = X_train.to(device)
X_test = X_test.to(device)
spectraVal = torch.tensor(spectraVal).float().to(device)   # Confusing names, these spectra are the 5000 spectra generated like the training dataset
#ValSpectra = torch.tensor(ValSpectra).float().to(device)   # Confusing names, these spectra are the 10 representative example spectra

# Move the target data to the GPU device
y_train = y_train.to(device)
y_test = y_test.to(device)
concVal = torch.tensor(concVal).float().to(device)
#ValConc = torch.tensor(ValConc).float().to(device)

# More data prep?
datasets = torch.utils.data.TensorDataset(X_train, y_train)
Test_datasets = torch.utils.data.TensorDataset(X_test, y_test)
Val_datasets = torch.utils.data.TensorDataset(spectraVal, concVal)
#train_iter = torch.utils.data.DataLoader(datasets, batch_size = 128, shuffle=True)
#test_iter = torch.utils.data.DataLoader(Test_datasets, batch_size = 128, shuffle=True)

In [6]:
del X_train
del X_test
del y_train
del y_test
del spectra
del conc1
del spectraVal
del concVal

In [7]:
class RelativeAbsoluteError(nn.Module):
    def __init__(self):
        super(RelativeAbsoluteError, self).__init__()

    def forward(self, y_pred, y_true):
        # Compute the mean of the true values
        y_mean = torch.mean(y_true)
        
        # Compute the absolute differences
        absolute_errors = torch.abs(y_true - y_pred)
        mean_absolute_errors = torch.abs(y_true - y_mean)
        
        # Compute RAE
        rae = torch.sum(absolute_errors) / torch.sum(mean_absolute_errors)
        return rae
    
    
    
# MAPE loss function for directly comparing models despite loss function used
class MAPELoss(nn.Module):
    def __init__(self):
        super(MAPELoss, self).__init__()

    def forward(self, y_pred, y_true):
        loss = torch.mean(torch.abs((y_true - y_pred) / y_true))
        return loss * 100  # To get percentage

In [ ]:
lr=0.00014656680844397094, weight_decay=0.01

In [8]:
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, max_len=5000):
        super(PositionalEncoding, self).__init__()
        self.d_model = d_model
        pe = torch.zeros(max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-np.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0).transpose(0, 1)
        self.register_buffer('pe', pe)

    def forward(self, x):
        return x + self.pe[:x.size(0), :]
    

class Transformer(nn.Module):
    def __init__(self, input_dim, d_model, nhead, num_encoder_layers, dim_feedforward, dropout):
        super(Transformer, self).__init__()
        self.input_dim = input_dim
        self.d_model = d_model
        self.embedding = nn.Linear(input_dim, d_model)
        self.positional_encoding = PositionalEncoding(d_model)
        encoder_layer = nn.TransformerEncoderLayer(d_model=d_model, nhead=nhead, dim_feedforward=dim_feedforward, dropout=dropout)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=num_encoder_layers)

    def forward(self, x):
        # Binning
        batch_size, seq_length = x.size()
        num_bins = seq_length // self.input_dim
        x = x.view(batch_size, num_bins, self.input_dim)  # (batch_size, num_bins, input_dim)
        
        # Embedding
        x = self.embedding(x)  # (batch_size, num_bins, d_model)
        
        # Add positional encoding
        x = self.positional_encoding(x)
        
        # Transformer Encoder
        x = x.permute(1, 0, 2)  # (num_bins, batch_size, d_model)
        x = self.transformer_encoder(x)  # (num_bins, batch_size, d_model)
        x = x.permute(1, 0, 2)  # (batch_size, num_bins, d_model)
        
        # Reconstruct original sequence
        x = x.reshape(batch_size, num_bins * self.d_model)
        
        # Initialize decoder if not already done
        if not hasattr(self, 'decoder'):
            self.decoder = nn.Linear(num_bins * self.d_model, 44).to(device)
        
        # Decoding
        x = self.decoder(x)  # (batch_size, output_dim)
        
        return x
    
    

In [9]:
512/np.array([1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16])

array([512.        , 256.        , 170.66666667, 128.        ,
       102.4       ,  85.33333333,  73.14285714,  64.        ,
        56.88888889,  51.2       ,  46.54545455,  42.66666667,
        39.38461538,  36.57142857,  34.13333333,  32.        ])

In [ ]:
# Switch to directory for saving weights
os.chdir('/home/htjhnson/Desktop/DL-NMR-Optimization/ModelOptimizations/BestWeights')
loaded_study = optuna.load_study(study_name="Transformer_Optuna_ForManuscript", storage="sqlite:///Transformer_Optuna_ForManuscript.db")

In [ ]:
## Optimization function

# Switch to directory for saving weights
os.chdir('/home/htjhnson/Desktop/DL-NMR-Optimization/ModelOptimizations/BestWeights')

# Define file name for best model weights
save_path = ModelName + '_Params.pt'




# Define an objective function to be minimized.
def objective(trial):
    
    # Suggest values of the hyperparameters using a trial object.
    n_layers = trial.suggest_int('n_layers', 1, 2)
    input_dim = trial.suggest_categorical('input_dim', [100, 200, 500, 1000, 2000])  # Size of each bin
    d_model = trial.suggest_categorical('d_model', [256, 512, 1024])     # Embedding dimension
    nhead = trial.suggest_categorical('nhead', [1, 2, 4, 8, 16])     # Number of attention heads
    num_encoder_layers = trial.suggest_int('num_encoder_layers', 1, 9)  # Number of transformer encoder layers
    dim_feedforward = trial.suggest_categorical('dim_feedforward', [512, 1024, 2048])  # Feedforward dimension
    dropout = 0    # Dropout rate
 
    
    
    # Create model
    model = Transformer(input_dim, d_model, nhead, num_encoder_layers, dim_feedforward, dropout)
    model.to(device)  # Move the model to the GPU    

        
    ## Split training data
    bs = trial.suggest_int("bs", 8, 128)
    train_loader = torch.utils.data.DataLoader(datasets, batch_size=bs, shuffle=True)
    test_loader = torch.utils.data.DataLoader(Test_datasets, batch_size=bs, shuffle=False)
    val_loader = torch.utils.data.DataLoader(Val_datasets, batch_size=bs, shuffle=False)
    accumulation_steps = 4
        
    
    # Train and evaluate the model to obtain the loss
    learning_rate = trial.suggest_float('learning_rate', 1e-6, 1e-2)
    reg_strength = trial.suggest_float('reg_strength', 1e-6, 1e-2)
    optimizer = torch.optim.AdamW(model.parameters(), lr=learning_rate, weight_decay=reg_strength)
    
    
    num_epochs = 700
    
    criterion = RelativeAbsoluteError()
    criterion2 = MAPELoss()
    best_test_loss = float('inf')
    start = time.time()

    for epoch in range(num_epochs):
        start2 = time.time()
        running_train_loss = 0.0
        running_test_loss = 0.0
                
        model.train()
        scaler = GradScaler()
        optimizer.zero_grad()
        for batch_idx, (inputs, labels) in enumerate(train_loader):
            inputs, labels = inputs.to(device), labels.to(device)
            with autocast():
                outputs = model(inputs)
                loss = criterion(outputs, labels)
                loss = loss / accumulation_steps
            running_train_loss += loss.item() * inputs.size(0)
            scaler.scale(loss).backward()

            if (batch_idx + 1) % accumulation_steps == 0:
                scaler.step(optimizer)
                scaler.update()
                optimizer.zero_grad()
        
        model.eval()
        test_loss = 0.0
        with torch.no_grad():
            for inputs, labels in test_loader:
                inputs, labels = inputs.to(device), labels.to(device)
                with autocast():
                    outputs = model(inputs)
                    loss = criterion(outputs, labels)
                running_test_loss += loss.item() * inputs.size(0)

        running_test_loss2 = 0.0
        with torch.no_grad():
            for inputs, labels in val_loader:
                inputs, labels = inputs.to(device), labels.to(device)
                with autocast():
                    outputs = model(inputs)
                    loss2 = criterion2(outputs, labels)
                running_test_loss2 += loss2.item() * inputs.size(0)
        
        if epoch % 1 == 0:
            end_time2 = time.time()
            print(f'Epoch {epoch + 1}/{num_epochs} | Train Loss: {running_train_loss:.3f} | Test Loss: {running_test_loss:.3f} | Test Loss [MAPE]: {running_test_loss2:.3f}', "--time--", end_time2-start2)

        if running_test_loss2 < best_test_loss:
            best_test_loss = running_test_loss2
            
        trial.report(running_test_loss, epoch)
        
        # Double threshold pruner
        if epoch > 15 and running_test_loss > 2000 and trial.should_prune():
            raise optuna.TrialPruned()
        elif epoch > 100 and running_test_loss > 1000 and trial.should_prune():
            raise optuna.TrialPruned()
            
        # Check for NaN values in the loss
        if np.isnan(running_test_loss):
            print(f"NaN detected in loss at epoch {epoch}. Stopping trial.")
            raise optuna.TrialPruned()            
            
            
    end_time = time.time()
    print(end_time - start)   

    return best_test_loss

study_name = "Transformer_Optuna_ForManuscript"
storage = "sqlite:///Transformer_Optuna_ForManuscript.db"  # SQLite database as storage
study = optuna.create_study(direction='minimize',  sampler=optuna.samplers.TPESampler(seed=5), 
                            study_name=study_name, storage=storage,
                            pruner=optuna.pruners.ThresholdPruner(upper = 1000))

study.optimize(objective, n_trials=100)

[I 2024-08-06 07:21:52,665] A new study created in RDB with name: Transformer_Optuna_ForManuscript


Epoch 1/700 | Train Loss: 2629.806 | Test Loss: 2572.792 | Test Loss [MAPE]: 512627.658 --time-- 4.715425252914429
Epoch 2/700 | Train Loss: 2566.281 | Test Loss: 2571.535 | Test Loss [MAPE]: 472408.951 --time-- 4.682740688323975
Epoch 3/700 | Train Loss: 2565.792 | Test Loss: 2572.458 | Test Loss [MAPE]: 508181.895 --time-- 4.690558910369873
Epoch 4/700 | Train Loss: 2566.916 | Test Loss: 2572.483 | Test Loss [MAPE]: 502772.863 --time-- 4.692997217178345
Epoch 5/700 | Train Loss: 2566.047 | Test Loss: 2571.811 | Test Loss [MAPE]: 471429.561 --time-- 4.7013609409332275
Epoch 6/700 | Train Loss: 2566.428 | Test Loss: 2572.631 | Test Loss [MAPE]: 501720.266 --time-- 4.701842784881592
Epoch 7/700 | Train Loss: 2565.106 | Test Loss: 2572.366 | Test Loss [MAPE]: 480846.829 --time-- 4.70311164855957
Epoch 8/700 | Train Loss: 2565.174 | Test Loss: 2571.934 | Test Loss [MAPE]: 480878.057 --time-- 4.708145618438721
Epoch 9/700 | Train Loss: 2565.489 | Test Loss: 2571.813 | Test Loss [MAPE]: 478

[I 2024-08-06 07:23:14,220] Trial 0 pruned. 


Epoch 17/700 | Train Loss: 2566.622 | Test Loss: 2571.467 | Test Loss [MAPE]: 462242.489 --time-- 4.720214605331421
Epoch 1/700 | Train Loss: 2665.061 | Test Loss: 2575.330 | Test Loss [MAPE]: 592342.776 --time-- 4.058625936508179
Epoch 2/700 | Train Loss: 2565.426 | Test Loss: 2570.372 | Test Loss [MAPE]: 462801.989 --time-- 4.034681081771851
Epoch 3/700 | Train Loss: 2563.581 | Test Loss: 2569.636 | Test Loss [MAPE]: 433731.496 --time-- 4.039556980133057
Epoch 4/700 | Train Loss: 2563.572 | Test Loss: 2569.462 | Test Loss [MAPE]: 424664.025 --time-- 4.03796124458313
Epoch 5/700 | Train Loss: 2562.916 | Test Loss: 2569.600 | Test Loss [MAPE]: 422416.923 --time-- 4.0391294956207275
Epoch 6/700 | Train Loss: 2563.967 | Test Loss: 2570.663 | Test Loss [MAPE]: 468189.254 --time-- 4.041089057922363
Epoch 7/700 | Train Loss: 2565.925 | Test Loss: 2571.246 | Test Loss [MAPE]: 500982.554 --time-- 4.038517236709595
Epoch 8/700 | Train Loss: 2565.246 | Test Loss: 2572.782 | Test Loss [MAPE]: 53

[I 2024-08-06 07:24:23,163] Trial 1 pruned. 


...

Epoch 142/700 | Train Loss: 210.889 | Test Loss: 251.180 | Test Loss [MAPE]: 1289134.104 --time-- 4.120383262634277
Epoch 143/700 | Train Loss: 207.339 | Test Loss: 250.745 | Test Loss [MAPE]: 1286139.977 --time-- 4.336592435836792
Epoch 144/700 | Train Loss: 207.366 | Test Loss: 256.322 | Test Loss [MAPE]: 1279266.812 --time-- 4.313755035400391
Epoch 145/700 | Train Loss: 207.253 | Test Loss: 247.857 | Test Loss [MAPE]: 1273252.911 --time-- 4.3247621059417725
Epoch 146/700 | Train Loss: 203.869 | Test Loss: 248.925 | Test Loss [MAPE]: 1266549.580 --time-- 4.309007167816162
Epoch 147/700 | Train Loss: 204.952 | Test Loss: 251.917 | Test Loss [MAPE]: 1291567.126 --time-- 4.1198410987854
Epoch 148/700 | Train Loss: 204.397 | Test Loss: 251.407 | Test Loss [MAPE]: 1307906.811 --time-- 3.907050371170044
Epoch 149/700 | Train Loss: 201.976 | Test Loss: 248.667 | Test Loss [MAPE]: 1270822.309 --time-- 3.9794921875
Epoch 150/700 | Train Loss: 198.958 | Test Loss: 248.802 | Test Loss [MAPE]: 1

Epoch 213/700 | Train Loss: 156.070 | Test Loss: 204.748 | Test Loss [MAPE]: 1051515.064 --time-- 4.166216850280762
Epoch 214/700 | Train Loss: 153.839 | Test Loss: 200.194 | Test Loss [MAPE]: 1069352.919 --time-- 4.231853246688843
Epoch 215/700 | Train Loss: 150.826 | Test Loss: 205.454 | Test Loss [MAPE]: 1075133.686 --time-- 4.24901819229126
Epoch 216/700 | Train Loss: 149.034 | Test Loss: 204.346 | Test Loss [MAPE]: 1113547.989 --time-- 4.16399884223938
Epoch 217/700 | Train Loss: 150.855 | Test Loss: 197.229 | Test Loss [MAPE]: 1081289.868 --time-- 4.2080488204956055
Epoch 218/700 | Train Loss: 147.944 | Test Loss: 200.381 | Test Loss [MAPE]: 1089617.969 --time-- 4.329392671585083
Epoch 219/700 | Train Loss: 144.733 | Test Loss: 198.766 | Test Loss [MAPE]: 1076274.111 --time-- 4.4245429039001465
Epoch 220/700 | Train Loss: 150.851 | Test Loss: 198.936 | Test Loss [MAPE]: 1047965.731 --time-- 4.600374937057495
Epoch 221/700 | Train Loss: 146.534 | Test Loss: 200.426 | Test Loss [MA

Epoch 284/700 | Train Loss: 122.794 | Test Loss: 177.153 | Test Loss [MAPE]: 983785.972 --time-- 4.309826612472534
Epoch 285/700 | Train Loss: 121.153 | Test Loss: 181.831 | Test Loss [MAPE]: 971513.727 --time-- 4.41193151473999
Epoch 286/700 | Train Loss: 121.978 | Test Loss: 178.408 | Test Loss [MAPE]: 970489.263 --time-- 4.085716009140015
Epoch 287/700 | Train Loss: 121.608 | Test Loss: 178.455 | Test Loss [MAPE]: 989825.026 --time-- 4.291241645812988
Epoch 288/700 | Train Loss: 122.117 | Test Loss: 180.939 | Test Loss [MAPE]: 1014782.517 --time-- 4.27388596534729
Epoch 289/700 | Train Loss: 127.109 | Test Loss: 187.383 | Test Loss [MAPE]: 1038408.158 --time-- 4.083767652511597
Epoch 290/700 | Train Loss: 127.612 | Test Loss: 181.582 | Test Loss [MAPE]: 1028503.445 --time-- 4.269039869308472
Epoch 291/700 | Train Loss: 123.685 | Test Loss: 177.961 | Test Loss [MAPE]: 1009427.776 --time-- 4.264921188354492
Epoch 292/700 | Train Loss: 120.619 | Test Loss: 181.486 | Test Loss [MAPE]: 1

Epoch 356/700 | Train Loss: 109.570 | Test Loss: 169.733 | Test Loss [MAPE]: 950663.587 --time-- 4.090059757232666
Epoch 357/700 | Train Loss: 107.763 | Test Loss: 172.855 | Test Loss [MAPE]: 967908.229 --time-- 4.1865339279174805
Epoch 358/700 | Train Loss: 106.774 | Test Loss: 168.102 | Test Loss [MAPE]: 936739.402 --time-- 4.283513069152832
Epoch 359/700 | Train Loss: 104.676 | Test Loss: 167.910 | Test Loss [MAPE]: 978149.787 --time-- 4.3431360721588135
Epoch 360/700 | Train Loss: 107.300 | Test Loss: 169.396 | Test Loss [MAPE]: 939136.484 --time-- 4.468766689300537
Epoch 361/700 | Train Loss: 106.892 | Test Loss: 172.024 | Test Loss [MAPE]: 974985.858 --time-- 4.2698633670806885
Epoch 362/700 | Train Loss: 105.909 | Test Loss: 166.480 | Test Loss [MAPE]: 919555.658 --time-- 4.310973644256592
Epoch 363/700 | Train Loss: 108.431 | Test Loss: 175.067 | Test Loss [MAPE]: 974339.915 --time-- 4.29518985748291
Epoch 364/700 | Train Loss: 108.522 | Test Loss: 167.122 | Test Loss [MAPE]: 9

Epoch 428/700 | Train Loss: 95.175 | Test Loss: 161.191 | Test Loss [MAPE]: 903994.494 --time-- 4.335527420043945
Epoch 429/700 | Train Loss: 112.163 | Test Loss: 165.595 | Test Loss [MAPE]: 919707.597 --time-- 4.111814498901367
Epoch 430/700 | Train Loss: 99.850 | Test Loss: 162.547 | Test Loss [MAPE]: 907407.929 --time-- 4.361009359359741
Epoch 431/700 | Train Loss: 99.203 | Test Loss: 165.927 | Test Loss [MAPE]: 943414.038 --time-- 4.120302200317383
Epoch 432/700 | Train Loss: 107.597 | Test Loss: 164.983 | Test Loss [MAPE]: 933241.716 --time-- 4.250935077667236
Epoch 433/700 | Train Loss: 97.672 | Test Loss: 161.663 | Test Loss [MAPE]: 934365.446 --time-- 4.260110378265381
Epoch 434/700 | Train Loss: 98.065 | Test Loss: 163.398 | Test Loss [MAPE]: 929678.706 --time-- 4.50502347946167
Epoch 435/700 | Train Loss: 98.467 | Test Loss: 164.866 | Test Loss [MAPE]: 915739.801 --time-- 4.4714155197143555
Epoch 436/700 | Train Loss: 95.134 | Test Loss: 160.796 | Test Loss [MAPE]: 921092.814

In [9]:
# Get the best parameters and best value from the study
best_params = loaded_study.best_params
best_value = loaded_study.best_value

# Create a dictionary to store hyperparameters and best loss
data = {
    'Hyperparameter': list(best_params.keys()) + ['Best Loss'],
    'Value': list(best_params.values()) + [best_value]
}

# Create a pandas DataFrame
df = pd.DataFrame(data)

# Display the DataFrame
print(df)

       Hyperparameter        Value
0            n_layers     1.000000
1           input_dim    50.000000
2  num_encoder_layers    16.000000
3               nhead     2.000000
4     dim_feedforward   512.000000
5             dropout     0.100000
6           Best Loss  2963.330837


In [19]:
optuna.visualization.plot_optimization_history(study)

In [20]:
optuna.visualization.plot_parallel_coordinate(study)

In [21]:
optuna.visualization.plot_param_importances(study)

In [22]:
optuna.visualization.plot_contour(study)

[W 2024-05-20 15:19:03,221] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,222] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,224] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,226] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,228] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,230] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,231] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,233] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,233] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,234] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,234] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,234] Param n_units_l3 unique value length is less than 2.
[W 2024-05-20 15:19:03,235] 

In [23]:
optuna.visualization.plot_rank(study)

/tmp/ipykernel_22839/1428420439.py:1: ExperimentalWarning:

plot_rank is experimental (supported from v3.2.0). The interface can change in the future.



In [24]:
optuna.visualization.plot_slice(study)

In [25]:
optuna.visualization.plot_terminator_improvement(study)

/tmp/ipykernel_22839/4136363031.py:1: ExperimentalWarning:

plot_terminator_improvement is experimental (supported from v3.2.0). The interface can change in the future.

/home/htjhnson/anaconda3/lib/python3.11/site-packages/optuna/visualization/_terminator_improvement.py:131: ExperimentalWarning:

RegretBoundEvaluator is experimental (supported from v3.2.0). The interface can change in the future.

/home/htjhnson/anaconda3/lib/python3.11/site-packages/optuna/visualization/_terminator_improvement.py:136: ExperimentalWarning:

CrossValidationErrorEvaluator is experimental (supported from v3.2.0). The interface can change in the future.

100%|███████████████████████████████████████████| 50/50 [00:01<00:00, 27.50it/s]


In [26]:
optuna.visualization.plot_timeline(study)

/tmp/ipykernel_22839/2497081126.py:1: ExperimentalWarning:

plot_timeline is experimental (supported from v3.2.0). The interface can change in the future.



In [27]:
optuna.visualization.plot_edf(study)

In [10]:
# Define file name for best model weights
save_path = ModelName + '_Params.pt'

In [11]:
def get_best_model(study):
    # Get the best trial
    best_trial = loaded_study.best_trial
    
    # Extract the best parameters
    best_params = best_trial.params
    
    # Load the entire dictionary from the saved file
    checkpoint = torch.load(save_path)
    
    # Load the model architecture from the checkpoint
    model_architecture = checkpoint['model_architecture']
    
    # Initialize the model and move it to the appropriate device
    model = model_architecture.to(device)
    
    # Load the model's state dictionary from the loaded dictionary
    model.load_state_dict(checkpoint['model_state_dict'])

    return model

best_model = get_best_model(loaded_study).eval()

In [12]:
criterion = torch.nn.MSELoss()


test_loader = torch.utils.data.DataLoader(datasets, batch_size=203, shuffle=False)
TheLoss = 0

# Testing phase
best_model.eval()
with torch.no_grad():
    for inputs, labels in test_loader:
        inputs, labels = inputs.to(device), labels.to(device)  # Move input data to the GPU
        outputs = best_model(inputs)
        loss = criterion(outputs, labels)
        TheLoss += loss.item()
        
TheLoss

KeyboardInterrupt: 

In [13]:
X_train[0].unsqueeze(0).size()

torch.Size([1, 46000])

In [28]:
X_train[0].unsqueeze(0)

tensor([[-0.0002, -0.0003, -0.0002,  ..., -0.0002, -0.0002, -0.0002]],
       device='cuda:0')

In [14]:
ValSpectra = torch.tensor(ValSpectra).float().to(device)   # Confusing names, these spectra are the 10 representative example spectra
ValConc = torch.tensor(ValConc).float().to(device)

In [15]:
best_model(X_train[0].unsqueeze(0))

tensor([[ 0.4690, 50.8730, 38.2940, 14.0805, 31.4338, 14.4011, 26.9853, 14.2782,
         31.5773, 40.6123, 38.7923, 19.2858, 32.5788, 24.2266, 30.5348, 29.2473,
         28.7214, 17.0446,  5.3141, 47.5459, 37.8027, 53.8406,  1.9025, 16.0109,
         29.9604, 27.3293, 37.9576, 40.6921, 35.1401, 33.0911, 36.1209, 42.3016,
         36.5444, 51.3456,  7.2974, 13.1087,  9.6610, 20.1943, 32.2622, -0.9763,
         38.8739, 39.0690, 41.9187, 47.4825]], device='cuda:0',
       grad_fn=<AddmmBackward0>)

In [16]:
y_train[0]

tensor([ 4.0717, 49.5768, 38.3677, 11.3346, 22.3017, 12.9476, 16.9491, 16.3040,
        34.2957, 40.2190, 36.4923, 17.5898, 24.9011, 18.9798, 31.6682, 30.6385,
        27.1793, 15.0093,  3.1209, 42.3842, 37.3571, 47.2943,  1.7990, 14.4903,
        27.5353, 31.2422, 38.8733, 37.4527, 35.7897, 33.2167, 32.0472, 36.9620,
        35.3223, 49.3332,  7.2213,  8.1352,  9.6507, 18.3274, 29.5438,  2.0174,
        36.3401, 34.8497, 44.4357, 42.3643], device='cuda:0')

In [18]:
## Switch to directory for saving model metrics

os.chdir('/home/htjhnson/Desktop/DL-NMR-Optimization/ModelPerformanceMetrics')   

In [47]:
## Test model on testing dataset and deterine RMSE

outputs = best_model(X_train) # Evaluate input spectra with MLP

# Move tensors to CPU and convert to numpy arrays
outputs_cpu = outputs.detach().cpu().numpy()
y_train_cpu = y_train.detach().cpu().numpy()

err = np.sqrt(mean_squared_error(outputs_cpu, y_train_cpu))  # Determine RMSE
print('model err: ', err)  # Print RMSE

np.save(ModelName + "TrainRMSE",err)

model err:  0.5982649


In [48]:
## Test model on testing dataset and deterine RMSE

best_model.eval() # Change to evaluation mode (maybe not needed for this model)
outputs = best_model(X_test) # Evaluate input spectra with MLP

# Move tensors to CPU and convert to numpy arrays
outputs_cpu = outputs.detach().cpu().numpy()
y_test_cpu = y_test.detach().cpu().numpy()

err = np.sqrt(mean_squared_error(outputs_cpu, y_test_cpu))  # Determine RMSE
print('model err: ', err)  # Print RMSE

np.save(ModelName + "TestRMSE",err)

model err:  1.1892706


In [19]:
APEs = []
MAPEs = []

for i in np.arange(10):
    GroundTruth = ValConc[i]
    Prediction = best_model(ValSpectra[i])

    # Move Prediction tensor to CPU and detach from computation graph
    Prediction_cpu = Prediction.detach().cpu().numpy()

    APE = []

    for metabolite in range(44):
        per_err = 100*(GroundTruth[metabolite] - Prediction_cpu[0][metabolite]) / GroundTruth[metabolite]
        APE.append(abs(per_err.cpu()))

    MAPE = sum(APE) / len(APE)

    APEs.append(APE)
    MAPEs.append(MAPE)


# Convert lists to numpy arrays and save
np.save(ModelName + "_" + "ValExamples_APEs.npy", np.array(APEs))
np.save(ModelName + "_" + "ValExamples_MAPEs.npy", np.array(MAPEs))


In [20]:
for i in np.arange(10):
    print(round(MAPEs[i].item(), 2), " - ",ValSpecNames[i])

763.06  -  AllAq1
53.25  -  AllAq5
8.62  -  AllAq25
13.46  -  AllAq50
9.38  -  ThreeAddedSinglets
15.89  -  ThirtyAddedSinglets
49.13  -  ShiftedSpec
74.83  -  SineBase
767.16  -  HighDynamicRange
inf  -  HalfZeros


In [56]:
APEs[-2]

[tensor(29474.),
 tensor(579.2571),
 tensor(62707.9102),
 tensor(226.6223),
 tensor(2321.5312),
 tensor(911.2342),
 tensor(40023.7969),
 tensor(1387.1711),
 tensor(43893.8867),
 tensor(713.6614),
 tensor(55314.2227),
 tensor(157.5777),
 tensor(35300.4023),
 tensor(315.0985),
 tensor(11870.5234),
 tensor(606.8740),
 tensor(26718.9004),
 tensor(906.0396),
 tensor(13471.4541),
 tensor(237.5626),
 tensor(42715.2148),
 tensor(399.1284),
 tensor(54354.8906),
 tensor(470.3720),
 tensor(35856.0117),
 tensor(850.3386),
 tensor(70786.6641),
 tensor(900.6191),
 tensor(23467.1230),
 tensor(541.4528),
 tensor(27273.9141),
 tensor(443.4006),
 tensor(57118.4375),
 tensor(380.6929),
 tensor(31198.1348),
 tensor(531.7195),
 tensor(52477.7539),
 tensor(872.3694),
 tensor(57572.7773),
 tensor(491.9031),
 tensor(2614.0620),
 tensor(1166.9354),
 tensor(1914.4690),
 tensor(1047.4916)]